In [1]:
import sys
sys.path.append("/Users/rohan/public_html/Hegemon")
import StepMiner as smn
import HegemonUtil as hu
import re
import numpy as np
import scipy
import io
from scipy import io
import math
import itertools
from itertools import combinations 
import matplotlib.pyplot as plt
%matplotlib inline
from matplotlib.backends.backend_pdf import PdfPages
import pandas as pd
import statsmodels.stats.proportion
import seaborn as sns
import scanpy as sc
import GEOparse
import os

In [20]:
# files are stored in subfolders for each gsm (lane)
directory = "counts"

for subdir, dirs, files in os.walk(directory):
    for file in files:
        mtxName = file.split(".")[0]
        if "matrix" in mtxName:
            print(file)

._lane2.mtx.colnames
lane2.mtx.rownames
lane2.mtx.colnames
._lane2.mtx.rownames
lane2-matrix.mtx
._lane2-matrix.mtx
._lane1.mtx.rownames
._lane1-matrix.mtx
lane1-matrix.mtx
._lane1.mtx.colnames
.DS_Store
._.DS_Store
lane1.mtx.colnames
lane1.mtx.rownames
lane7.mtx.rownames
._lane7.mtx.rownames
lane7-matrix.mtx
lane7.mtx.colnames
._lane7.mtx.colnames
._lane7-matrix.mtx
lane4-matrix.mtx
._lane4-matrix.mtx
._lane4.mtx.colnames
._lane4.mtx.rownames
lane4.mtx.rownames
lane4.mtx.colnames
._lane6-matrix.mtx
lane6.mtx.colnames
lane6-matrix.mtx
lane6.mtx.rownames
._lane6.mtx.colnames
._lane6.mtx.rownames
._lane3.mtx.colnames
lane3.mtx.colnames
._lane3.mtx.rownames
lane3-matrix.mtx
lane3.mtx.rownames
._lane3-matrix.mtx
lane8.mtx.rownames
._lane8.mtx.rownames
lane8-matrix.mtx
lane8.mtx.colnames
._lane8-matrix.mtx
._lane8.mtx.colnames
._lane5.mtx.colnames
._lane5.mtx.rownames
lane5.mtx.colnames
._lane5-matrix.mtx
lane5-matrix.mtx
lane5.mtx.rownames


In [2]:
# Read sparse matrices and assemble to matrix file

laneToGSM = {"lane1":"GSM5106951", "lane2":"GSM5106952", "lane3":"GSM5106953", \
              "lane4":"GSM5106954", "lane5":"GSM5106955", "lane6":"GSM5106956", \
              "lane7":"GSM5106957", "lane8":"GSM5106958"}

directory = "counts"

expr = pd.DataFrame()
expr["ProbeID"] = 0

for subdir, dirs, files in os.walk(directory):
    #for dir in dirs:
        #print(os.path.join(subdir, dir))
    for file in files:
        #print(os.path.join(root, file))
        #print(file)
        mtxName = file.split(".")[0]
        if "matrix" in mtxName:
            print(file)
            count_mtx = (scipy.io.mmread(subdir+"/"+mtxName+".mtx"))
            count_mtx = pd.DataFrame.sparse.from_spmatrix(count_mtx)
            
            lane = mtxName.split("-")[0]
            print(laneToGSM[lane])
            count_mtx.columns = [laneToGSM[lane]]*len(count_mtx.columns)            
            # to add cell barcodes as headers
            #f = open(subdir+"/"+mtxName+".mtx.colnames", 'r')
            #count_mtx.columns = [x.strip() for x in f.readlines()]
            #f.close() 
            
            f = open(subdir+"/"+lane+".mtx.rownames", 'r')
            genes = pd.Series([x.strip() for x in f.readlines()])
            f.close()
            count_mtx.insert(0, "ProbeID", genes) 
            
            expr = expr.merge(count_mtx, how="outer", on="ProbeID")

ensembl_df = pd.DataFrame(pd.read_csv("/booleanfs2/sahoo/Data/SeqData/genome/Homo_sapiens.GRCh38.99.chr_patch_hapl_scaff.txt", sep = '\t', header=None)) 
ensembl_df.columns = ["ProbeID", "Name"]
expr = ensembl_df.merge(expr, how="right",on="ProbeID")
expr

lane2-matrix.mtx
GSM5106952
lane1-matrix.mtx
GSM5106951
lane7-matrix.mtx
GSM5106957
lane4-matrix.mtx
GSM5106954
lane6-matrix.mtx
GSM5106956
lane3-matrix.mtx
GSM5106953
lane8-matrix.mtx
GSM5106958
lane5-matrix.mtx
GSM5106955


ProbeID         Name  GSM5106952  GSM5106952  GSM5106952  \
0      ENSG00000000003       TSPAN6           0           2           0   
1      ENSG00000000005         TNMD           0           0           0   
2      ENSG00000000419         DPM1           0           1           0   
3      ENSG00000000457        SCYL3           8          12          12   
4      ENSG00000000460     C1orf112           0           1           0   
...                ...          ...         ...         ...         ...   
35034  ENSG00000285480        H2BE1           0           0           0   
35035  ENSG00000285491  AC135068.11           0           0           0   
35036  ENSG00000285505   AC010616.1           0           0           0   
35037  ENSG00000285508   AL034430.1           0           0           0   
35038  ENSG00000285509   AP000646.1           0           0           0   

       GSM5106952  GSM5106952  GSM5106952  GSM5106952  GSM5106952  ...  \
0               0           0           1           0           0  ...   
1               0           0           0           0           0  ...   
2               0           0           0           0           0  ...   
3              11           8          30           7           5  ...   
4               1           1           0           0           0  ...   
...           ...         ...         ...         ...         ...  ...   
35034           0           0           0           0           0  ...   
35035           0           0           0           0           0  ...   
35036           0           0           0           0           0  ...   
35037           1           0           0           0           0  ...   
35038           0           0           0           0           0  ...   

       GSM5106955  GSM5106955  GSM5106955  GSM5106955  GSM5106955  GSM5106955  \
0               0           0           0           0           0           0   
1               0           0           0           0           0           0   
2               0           0           0           0           0           0   
3               0           0           0           0           1           0   
4               0           0           0           0           0           0   
...           ...         ...         ...         ...         ...         ...   
35034           0           0           0           0           0           0   
35035           0           0           0           0           0           0   
35036           0           0           0           0           0           0   
35037           0           0           0           0           0           0   
35038           0           0           0           0           0           0   

       GSM5106955  GSM5106955  GSM5106955  GSM5106955  
0               0           0           0           0  
1               0           0           0           0  
2               0           0           0           0  
3               0           0           0           0  
4               0           0           0           0  
...           ...         ...         ...         ...  
35034           0           0           0           0  
35035           0           0           0           0  
35036           0           0           0           0  
35037           0           0           0           0  
35038           0           0           0           0  

[35039 rows x 74630 columns]

In [14]:
print("Starting")

genes = pd.DataFrame()
genes["ProbeID"] = expr["ProbeID"]
genes["Name"] = expr["Name"]
cols = expr.columns

expr = expr.drop(['ProbeID', 'Name'], axis=1)
expr = sc.AnnData(expr.T)
sc.pp.normalize_total(expr, target_sum=1e6)
sc.pp.log1p(expr, base = 2)

expr = pd.DataFrame(expr.X)
expr = expr.T
expr.insert(0, "Name", genes["Name"])
expr.insert(0, "ProbeID", genes["ProbeID"])
expr.columns = cols
expr

path_dir = "./"
expr.to_csv(path_dir+"GSE167540-GPL16791-expr.txt", header=True, index=False,sep='\t')

Starting


In [15]:
expr

ProbeID         Name  GSM5106952  GSM5106952  GSM5106952  \
0      ENSG00000000003       TSPAN6    0.000000    5.769063    0.000000   
1      ENSG00000000005         TNMD    0.000000    0.000000    0.000000   
2      ENSG00000000419         DPM1    0.000000    4.795279    0.000000   
3      ENSG00000000457        SCYL3    7.645893    8.331809    8.397583   
4      ENSG00000000460     C1orf112    0.000000    4.795279    0.000000   
...                ...          ...         ...         ...         ...   
35034  ENSG00000285480        H2BE1    0.000000    0.000000    0.000000   
35035  ENSG00000285491  AC135068.11    0.000000    0.000000    0.000000   
35036  ENSG00000285505   AC010616.1    0.000000    0.000000    0.000000   
35037  ENSG00000285508   AL034430.1    0.000000    0.000000    0.000000   
35038  ENSG00000285509   AP000646.1    0.000000    0.000000    0.000000   

       GSM5106952  GSM5106952  GSM5106952  GSM5106952  GSM5106952  ...  \
0        0.000000    0.000000    4.939008    0.000000    0.000000  ...   
1        0.000000    0.000000    0.000000    0.000000    0.000000  ...   
2        0.000000    0.000000    0.000000    0.000000    0.000000  ...   
3        8.521584    7.957067    9.799704    8.026362    7.458399  ...   
4        5.100884    4.997146    0.000000    0.000000    0.000000  ...   
...           ...         ...         ...         ...         ...  ...   
35034    0.000000    0.000000    0.000000    0.000000    0.000000  ...   
35035    0.000000    0.000000    0.000000    0.000000    0.000000  ...   
35036    0.000000    0.000000    0.000000    0.000000    0.000000  ...   
35037    5.100884    0.000000    0.000000    0.000000    0.000000  ...   
35038    0.000000    0.000000    0.000000    0.000000    0.000000  ...   

       GSM5106955  GSM5106955  GSM5106955  GSM5106955  GSM5106955  GSM5106955  \
0             0.0         0.0         0.0         0.0    0.000000         0.0   
1             0.0         0.0         0.0         0.0    0.000000         0.0   
2             0.0         0.0         0.0         0.0    0.000000         0.0   
3             0.0         0.0         0.0         0.0   13.392544         0.0   
4             0.0         0.0         0.0         0.0    0.000000         0.0   
...           ...         ...         ...         ...         ...         ...   
35034         0.0         0.0         0.0         0.0    0.000000         0.0   
35035         0.0         0.0         0.0         0.0    0.000000         0.0   
35036         0.0         0.0         0.0         0.0    0.000000         0.0   
35037         0.0         0.0         0.0         0.0    0.000000         0.0   
35038         0.0         0.0         0.0         0.0    0.000000         0.0   

       GSM5106955  GSM5106955  GSM5106955  GSM5106955  
0             0.0         0.0         0.0         0.0  
1             0.0         0.0         0.0         0.0  
2             0.0         0.0         0.0         0.0  
3             0.0         0.0         0.0         0.0  
4             0.0         0.0         0.0         0.0  
...           ...         ...         ...         ...  
35034         0.0         0.0         0.0         0.0  
35035         0.0         0.0         0.0         0.0  
35036         0.0         0.0         0.0         0.0  
35037         0.0         0.0         0.0         0.0  
35038         0.0         0.0         0.0         0.0  

[35039 rows x 74630 columns]

In [16]:
# Build idx file

def make_idx():
    print('Starting make_idx')
    expr = path_dir+'GSE167540-GPL16791-expr.txt'

    ptr = []
    ids = []
    name = []
    desc = []
    pos = 0

    with open(expr, 'rb') as f:
        for line in f:
            if pos == 0:
                pos += len(line)
            else:
                ptr.append(pos)
                pos += len(line)
                split = line.decode("utf-8").split('\t')
                ids.append(split[0])
                name.append(split[1].split(':')[0])
                desc.append(':'.join(split[1].split(':')[1:]))
        f.close()

    with open(path_dir+'GSE167540-GPL16791-idx.txt', 'w') as f:
        f.write('ProbeID\tPtr\tName\tDescription\n')
        for i in range(len(ids)):
            f.write('{}\t{}\t{}\t{}\n'.format(ids[i], ptr[i], name[i], desc[i]))
        f.close()
    print("Done with make_idx")
    
make_idx()

Starting make_idx
Done with make_idx
